In [5]:
import torch
import torch.nn as nn
from torch.nn import functional as F
import kagglehub
import os
import pandas as pd
import json
from transformers import GPT2Tokenizer
import re
from source.load_data import load, HarryDataset

In [1]:
import pkg_resources

# Liste des bibliothèques utilisées
packages = [
    "os", "torch", "torchtext", "tqdm", "numpy", "requests",
    "IPython", "matplotlib", "wordcloud", "re", "string"
]

# Récupérer les versions
with open("requirements.txt", "w") as f:
    for package in packages:
        try:
            version = pkg_resources.get_distribution(package).version
            f.write(f"{package}=={version}\n")
        except pkg_resources.DistributionNotFound:
            print(f"⚠️  {package} n'est pas installé.")

⚠️  os n'est pas installé.
⚠️  re n'est pas installé.
⚠️  string n'est pas installé.


In [6]:
"coucou. je suis".split(".")

['coucou', ' je suis']

In [8]:
TEXT, texts = load()
dataset = re.split(r'(?<=[.!?])\s+', TEXT)

In [9]:
dataset

['M r.',
 'and Mrs.',
 'Dursley, of number four, Privet Drive, were proud to say that they were perfectly normal, thank you very much.',
 'They were the last people you’d expect to be involved in anything strange or mysterious, because they just didn’t hold with such nonsense.',
 'Mr.',
 'Dursley was the director of a firm called Grunnings, which made drills.',
 'He was a big, beefy man with hardly any neck, although he did have a very large mustache.',
 'Mrs.',
 'Dursley was thin and blonde and had nearly twice the usual amount of neck, which came in very useful as she spent so much of her time craning over garden fences, spying on the neighbors.',
 'The Dursleys had a small son called Dudley and in their opinion there was no finer boy anywhere.',
 'The Dursleys had everything they wanted, but they also had a secret, and their greatest fear was that somebody would discover it.',
 'They didn’t think they could bear it if anyone found out about the Potters.',
 'Mrs.',
 'Potter was Mrs.'

In [15]:
books = ["01 Harry Potter and the Sorcerers Stone",
         "02 Harry Potter and the Chamber of Secrets",
         "03 Harry Potter and the Prisoner of Azkaban",
         "04 Harry Potter and the Goblet of Fire",
         "05 Harry Potter and the Order of the Phoenix",
         "06 Harry Potter and the Half-Blood Prince",
         "07 Harry Potter and the Deathly Hallows"]
path = kagglehub.dataset_download("shubhammaindola/harry-potter-books")
texts = {}
TEXT = ""
for book in books:
    file_path = os.path.join(path, f"{book}.txt")
    with open(file_path, "r", encoding="utf-8") as f:
        text = f.read()
    TEXT += text
    texts[book] = text


In [16]:
TEXT

'M r. and Mrs. Dursley, of number four, Privet Drive, were proud to say that they were perfectly normal, thank you very much. They were the last people you’d expect to be involved in anything strange or mysterious, because they just didn’t hold with such nonsense.\n\nMr. Dursley was the director of a firm called Grunnings, which made drills. He was a big, beefy man with hardly any neck, although he did have a very large mustache. Mrs. Dursley was thin and blonde and had nearly twice the usual amount of neck, which came in very useful as she spent so much of her time craning over garden fences, spying on the neighbors. The Dursleys had a small son called Dudley and in their opinion there was no finer boy anywhere.\n\nThe Dursleys had everything they wanted, but they also had a secret, and their greatest fear was that somebody would discover it. They didn’t think they could bear it if anyone found out about the Potters. Mrs. Potter was Mrs. Dursley’s sister, but they hadn’t met for sever

In [18]:
tokenizer = GPT2Tokenizer.from_pretrained("gpt2")
tokens = tokenizer(text)
tokens

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

/opt/anaconda3/lib/python3.12/site-packages/huggingface_hub/file_download.py:1142: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (305068 > 1024). Running this sequence through the model will result in indexing errors


{'input_ids': [464, 734, 1450, 4120, 503, 286, 12062, 11, 257, 1178, 5695, 5475, 287, 262, 7135, 11, 8824, 18250, 11193, 13, 1114, 257, 1218, 484, 6204, 2407, 991, 11, 266, 1746, 7924, 379, 1123, 584, 338, 34572, 26, 788, 11, 22650, 1123, 584, 11, 484, 336, 6972, 511, 266, 1746, 11061, 511, 28050, 4730, 290, 2067, 6155, 35984, 306, 287, 262, 976, 4571, 13, 564, 250, 9980, 30, 447, 251, 1965, 262, 25242, 286, 262, 734, 13, 564, 250, 464, 1266, 11, 447, 251, 8712, 41343, 31008, 13, 383, 11193, 373, 275, 24071, 319, 262, 1364, 416, 4295, 11, 1877, 12, 25167, 275, 859, 7689, 11, 319, 262, 826, 416, 257, 1029, 11, 29776, 38705, 1522, 19859, 13, 383, 1450, 338, 890, 28050, 4730, 781, 6320, 1088, 511, 42415, 355, 484, 23558, 13, 564, 250, 817, 2917, 314, 1244, 307, 2739, 11, 447, 251, 531, 575, 897, 1636, 11, 465, 19861, 3033, 22292, 287, 290, 503, 286, 6504, 355, 262, 13737, 286, 625, 71, 4924, 7150, 6265, 262, 8824, 2971, 13, 564, 250, 1026, 373, 257, 1310, 6908, 959, 621, 314, 2938, 13, 88